In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans
import requests
import urllib
# !conda install -c conda-forge folium=0.11.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library
import seaborn as sns
from folium.plugins import HeatMap
%pylab inline
plt.style.use('fivethirtyeight')
print('Libraries imported.')

Populating the interactive namespace from numpy and matplotlib
Libraries imported.


In [3]:
!wget -q -O 'data/newyork_data.json' https://cocl.us/new_york_dataset 
print('Data downloaded!')

Data downloaded!


### Read data and fill DataFrame

In [4]:
with open('data/newyork_polygon.json') as json_data:
    newyork_data = json.load(json_data)
    

In [5]:
from ray_casting import *
def points_to_poly(points, name='default'):
    return Poly(name=name, edges=
        tuple(Edge(a=Pt(x=points[i0][0], y=points[i0][1]), b=Pt(x=points[i1][0], y=points[i1][1]))
        for i0,i1 in zip(range(len(points)),list(range(1,len(points))) + [0])))

In [6]:
ny_df = pd.DataFrame(columns=['Neighborhood','Borough','Longitude','Latitude','Polygon'])
GLOB_MIN = np.array([100000.0,10000])
GLOB_MAX = np.array([-100000.0,-10000])
for ng in newyork_data['features']:
    
    max_ = np.max(np.array(ng['geometry']['coordinates'][0]), axis = 0)
    min_ = np.min(np.array(ng['geometry']['coordinates'][0]), axis = 0)
    GLOB_MIN[0] = min(GLOB_MIN[0],min_[0])
    GLOB_MIN[1] = min(GLOB_MIN[1],min_[1])
    GLOB_MAX[0] = max(GLOB_MAX[0],max_[0])
    GLOB_MAX[1] = max(GLOB_MAX[1],max_[1])
    
    coords = min_ + (max_ - min_)/2
    ny_df.loc[-1] = [ng['properties']['neighborhood'],ng['properties']['borough']] + coords.tolist() +[points_to_poly(ng['geometry'][
    'coordinates'][0])]
        
    ny_df = ny_df.reset_index(drop=True)

ny_df['Borough']  = ny_df.Borough.astype('category')

ny_df['Borough_code'] = ny_df.Borough.cat.codes
#Convert long lat to xy-coordinates (linearized)
lat_conv = 0.69
long_conv = 0.52
ny_df['Latitude'] *= lat_conv
ny_df['Longitude'] *= long_conv

### Load subway data

In [7]:
subways_df = pd.read_csv('data/DOITT_SUBWAY_ENTRANCE_01_13SEPT2010.csv')

subways_df['Longitude'] = subways_df.the_geom.apply(lambda x: float(x.split()[1][1:]))
subways_df['Latitude'] = subways_df.the_geom.apply(lambda x: float(x.split()[2][:-1]))

subways_df = subways_df[['Longitude','Latitude']]
subways_df['Latitude'] *= lat_conv
subways_df['Longitude'] *= long_conv

### Set up grid covering NYC

In [8]:
Ym, Xm = np.meshgrid(*[np.linspace(GLOB_MIN[i],GLOB_MAX[i],100) for i in range(2)])

Filter for grid points that lie within neighborhoods

In [9]:
point_grid = []
for i,(x, y) in enumerate(zip(Xm.flatten(),Ym.flatten())):
    if i%1000 == 0:
        print('{} %'.format(int(i/100)))
    for neigh, poly in zip(ny_df.Neighborhood, ny_df.Polygon):
        if ispointinside(Pt(y,x),poly):  
            point_grid.append([neigh, x,y])

0 %
10 %
20 %
30 %
40 %
50 %
60 %
70 %
80 %
90 %


In [10]:
ny_df = ny_df.groupby(['Neighborhood']).mean().reset_index()

### For every grid point, find distance to closest subway station

In [11]:
from sklearn.neighbors import NearestNeighbors

point_grid_df = pd.DataFrame(point_grid, columns=['Neighborhood','Latitude','Longitude'])

nn = NearestNeighbors(1)

nn.fit(subways_df[['Latitude','Longitude']])

point_grid_df['subway_dist'] = nn.kneighbors(point_grid_df[['Latitude','Longitude']]*np.array([lat_conv,long_conv]))[0]

point_grid_df.head()

Neighborhood   Latitude  Longitude  subway_dist
0  Tottenville  40.500370 -74.249979     0.008238
1  Tottenville  40.500370 -74.244367     0.009221
2  Tottenville  40.500370 -74.238756     0.010903
3  Tottenville  40.504607 -74.249979     0.005388
4  Tottenville  40.504607 -74.244367     0.006798

In [13]:
world_map = folium.Map(location=[40.7896239, -73.9598939], zoom_start=11,width='100%',height='100%')



choropleth = folium.Choropleth(geo_data='data/newyork_polygon.json',key_on='feature.properties.neighborhood',
                    fill_color='YlOrRd', 
                    fill_opacity=0.7, 
                    line_opacity=1,
                    line_color='black').add_to(world_map)

for idx,(n,x,y,dist) in point_grid_df.iterrows():
        folium.CircleMarker(
                [x, y],
                radius=2,
                fill=True,
                color=colors.rgb2hex(cm.YlOrRd(dist*100)),
                fill_opacity=0.7).add_to(world_map)

    
world_map

### Take average distance to subway stations for grid points in every neighborhood

In [14]:
subway_dist_df = point_grid_df.groupby('Neighborhood').mean()[['subway_dist']]

subway_dist_df['quantile'] = pd.qcut(subway_dist_df.subway_dist,4,labels=np.arange(4))

In [15]:
world_map = folium.Map(location=[40.7896239, -73.9598939], zoom_start=11,width='100%',height='100%')



choropleth = folium.Choropleth(geo_data='data/newyork_polygon.json', 
                    data=subway_dist_df.reset_index(), columns=['Neighborhood','quantile'],key_on='feature.properties.neighborhood',
                    fill_color='YlOrRd', 
                    fill_opacity=0.7, 
                    line_opacity=1,
                    line_color='black').add_to(world_map)

choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['neighborhood'], labels=False)
)

world_map

In [16]:
subway_dist_df.to_csv('subway.csv')

In [17]:
world_map.save('fig/subway.html')